In [296]:
# For Question 1-Task 1
# Task 1: create interactive maps of housing loss for the census tracts of Hillsborough County, FL to display evictions/foreclosures/overall housing loss

# By Fubao Wu

# import library
import pandas as pd
import numpy as np
import gdown

!pip install geojson 
import geojson   # process geojson

import folium    # for interactive map
import branca


**Download Data**

In [297]:
# Download Hillsborough county data

# hillsborough_fl_2010_tracts_formatted
house_loss_Hillsborough_geojson_raw = "https://drive.google.com/file/d/1UvKEDzbn6rEhkke8j1dSZxbb1mRdYj0F/view?usp=sharing"
house_loss_Hillsborough_geojson = "hillsborough_fl_2010_tracts_formatted.geojson"
house_loss_Hillsborough_geojson_url = "https://drive.google.com/uc?id=" + house_loss_Hillsborough_geojson_raw.split('/')[-2]  #Do not change
gdown.download(house_loss_Hillsborough_geojson_url, house_loss_Hillsborough_geojson, quiet=False)  # Name of the file

# hillsborough_fl_processed_2017_to_2019_20210916
hillsborough_fl_processed_raw = "https://drive.google.com/file/d/1abt4fLPO__KxBLz9SXue5VKeZN3cUcCF/view?usp=sharing"
hillsborough_fl_processed_csv = "hillsborough_fl_processed_2017_to_2019_20210916.csv"
hillsborough_fl_processed_url = "https://drive.google.com/uc?id=" + hillsborough_fl_processed_raw.split('/')[-2]  #Do not change
gdown.download(hillsborough_fl_processed_url, hillsborough_fl_processed_csv, quiet=False)  # Name of the file


Downloading...
From: https://drive.google.com/uc?id=1UvKEDzbn6rEhkke8j1dSZxbb1mRdYj0F
To: /content/hillsborough_fl_2010_tracts_formatted.geojson
100%|██████████| 1.69M/1.69M [00:00<00:00, 102MB/s]
Downloading...
From: https://drive.google.com/uc?id=1abt4fLPO__KxBLz9SXue5VKeZN3cUcCF
To: /content/hillsborough_fl_processed_2017_to_2019_20210916.csv
100%|██████████| 207k/207k [00:00<00:00, 43.5MB/s]


'hillsborough_fl_processed_2017_to_2019_20210916.csv'

**Read Data**

In [298]:
# read Hillsborough geojson
with open(house_loss_Hillsborough_geojson) as f:
    gj_Hillsborough = geojson.load(f)
type(gj_Hillsborough)

geojson.feature.FeatureCollection

In [299]:
#print("gj_Hillsborough['features']: ", len(gj_Hillsborough['features']))
for feature in gj_Hillsborough['features']:
    #print(feature)
    print(feature.keys())
    print(feature['properties']['census_tract_GEOID'])
    print (feature['geometry']['coordinates'])
    print (feature['geometry']['type'])
    #print (feature['id'])
    break
  
#gj_Hillsborough['features']

gj_Hillsborough['features']:  321
dict_keys(['type', 'geometry', 'properties'])
12057006900
[[[-82.50651, 27.879119], [-82.506482, 27.877856], [-82.506462, 27.876876], [-82.506452, 27.876398], [-82.506431, 27.875541], [-82.506397, 27.873761], [-82.506369, 27.872621], [-82.506366, 27.871856], [-82.506356, 27.869037], [-82.506252, 27.869115], [-82.505717, 27.868859], [-82.505473, 27.868848], [-82.505281, 27.868704], [-82.504775, 27.868707], [-82.504767, 27.86824], [-82.50441, 27.868234], [-82.504391, 27.867775], [-82.503966, 27.867746], [-82.50379, 27.867734], [-82.50379, 27.867317], [-82.503351, 27.867312], [-82.503352, 27.867251], [-82.503044, 27.867254], [-82.502402, 27.867259], [-82.502251, 27.8673], [-82.502235, 27.864751], [-82.499789, 27.864633], [-82.49761, 27.864662], [-82.494144, 27.864607], [-82.494141, 27.864769], [-82.494136, 27.865143], [-82.494132, 27.865428], [-82.494038, 27.865353], [-82.493775, 27.865144], [-82.493778, 27.864676], [-82.488732, 27.86466], [-82.488423, 27

In [327]:
# read hillsborough_fl_processed_csv


df_hillsborough_fl_processed = pd.read_csv(hillsborough_fl_processed_csv)
# change census_tract_GEOID to string to match the Geojson file
df_hillsborough_fl_processed['census_tract_GEOID'] = df_hillsborough_fl_processed['census_tract_GEOID'].map(str) #  = df_hillsborough_fl_processed['census_tract_GEOID'].astype(str)

df_hillsborough_fl_processed.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 321 entries, 0 to 320
Data columns (total 73 columns):
 #   Column                                    Non-Null Count  Dtype  
---  ------                                    --------------  -----  
 0   census_tract_GEOID                        321 non-null    object 
 1   total-households                          321 non-null    int64  
 2   total-renter-occupied-households          321 non-null    int64  
 3   total-owner-occupied-households           321 non-null    int64  
 4   total-owner-occupied-households-mortgage  321 non-null    int64  
 5   median-gross-rent                         321 non-null    int64  
 6   median-household-income                   321 non-null    int64  
 7   median-property-value                     321 non-null    int64  
 8   median-monthly-housing-cost               321 non-null    int64  
 9   pct-white                                 321 non-null    int64  
 10  pct-af-am                             

In [301]:
df_hillsborough_fl_processed.head()

census_tract_GEOID  total-households  ...               county    state
0         12057000401               926  ...  Hillsborough County  Florida
1         12057010105              1496  ...  Hillsborough County  Florida
2         12057010203               766  ...  Hillsborough County  Florida
3         12057010600              1108  ...  Hillsborough County  Florida
4         12057002300              1419  ...  Hillsborough County  Florida

[5 rows x 73 columns]

In [302]:
# df_hillsborough_fl_processed.describe()


**Read Eviction,   Mark on Map with tooltip**

In [375]:
#  Marker on Map with tooltip 

#one_geoid = df_hillsborough_fl_processed['census_tract_GEOID'][0]
# print(one_geoid)


district_num  = len(gj_Hillsborough['features'])
one_center_lat_long = gj_Hillsborough['features'][district_num//2]['geometry']['coordinates'][0][0][::-1]
#print(one_center_lat_long)

map_type = 'Geo_Map'

if map_type == 'Geo_Map':

  map_Hillsborough = folium.Map(one_center_lat_long, zoom_start=10)
  folium.GeoJson(gj_Hillsborough).add_to(map_Hillsborough)
  # map_Hillsborough


  for feature in gj_Hillsborough['features']:
      #print(feature)
      #print(feature.keys())
      geoid = feature['properties']['census_tract_GEOID']
      #print(type(geoid))

      locations = feature['geometry']['coordinates']
      #print("locations: ", type(locations), len(locations), len(locations[0]), locations[0][0][::-1])
      eviction_total_num = df_hillsborough_fl_processed.loc[df_hillsborough_fl_processed['census_tract_GEOID'] == geoid, 'total-evictions'].item() 
      #print("total_eviction: ", eviction_total_num)
      marker_show = 'Total evictions: ' + str(eviction_total_num)
      folium.Marker(
          location= locations[0][0][::-1],
          popup=marker_show,
          icon=folium.Icon(icon='cloud'),
      ).add_to(map_Hillsborough)

# diplay map    
map_Hillsborough

In [372]:
# create Choropleeth map

map_type = 'Choropleth_map'

if map_type == 'Choropleth_map':

  map_choropleth_Hillsborough = folium.Map(location=one_center_lat_long, zoom_start=10)


  columns_shown = ['total-evictions', 'total-foreclosure-sales', 'avg-housing-loss-rate']
  
  for col_name in columns_shown:
    bins =  list(df_hillsborough_fl_processed['total-evictions'].quantile(np.linspace(0, 1, 6)))
    # choropleth
    folium.Choropleth(
        geo_data=gj_Hillsborough,
        name=col_name,
        data=df_hillsborough_fl_processed,
        columns=['census_tract_GEOID', col_name], # 'total-households'],  # 'total-evictions'],
        # see folium.Choropleth? for details on key_on
        key_on='feature.properties.census_tract_GEOID',     # 'feature.id',
        fill_color='RdYlBu', 
        nan_fill_color='G',
        fill_opacity=0.3,
        line_opacity=0.5,
        legend_name=col_name,
        highlight=True,
        # bins=bins # bins
    ).add_to(map_choropleth_Hillsborough)

  folium.LayerControl(collapsed=False).add_to(map_choropleth_Hillsborough)

# save map to html
map_choropleth_Hillsborough.save('map_choropleth_Hillsborough.html')

# display map
map_choropleth_Hillsborough